## Preprocess Bag of Words Lyrics
CS 230: Deep Learning 

Joe Sommer 12/8/2019

This script is for preprocessing data from the Million Song and musiXmatch datasets found here: 
http://millionsongdataset.com/
http://millionsongdataset.com/musixmatch/


It stores the lyrics and release years of songs with usable lyrics, and saves the resulting clean data
as a CSV file to be used to train different learning models to predict the decade a song was released in. 


In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

In [7]:
# lyrics from mxm_dataset_train.txt  
# release year info from tracks_per_year.txt

lyrics_info_unclean = []

f1 = open('mxm_dataset_train.txt','r')
lyrics_info_unclean = f1.readlines()
f1.close()

In [ ]:
lyrics_info = []
for l in lyrics_info_unclean:
    if l[0] != '#':
        lyrics_info.append(l)


In [60]:
# separate first line w/ the different words into a list
all_words = lyrics_info[0]
all_words = all_words[1:]  # removes % from beginning

word_list = all_words.split(',')
print(word_list)             

## need to save this as the full dictionary of words 

['i', 'the', 'you', 'to', 'and', 'a', 'me', 'it', 'not', 'in', 'my', 'is', 'of', 'your', 'that', 'do', 'on', 'are', 'we', 'am', 'will', 'all', 'for', 'no', 'be', 'have', 'love', 'so', 'know', 'this', 'but', 'with', 'what', 'just', 'when', 'like', 'now', 'que', 'time', 'can', 'come', 'de', 'there', 'go', 'up', 'oh', 'la', 'one', 'they', 'out', 'down', 'get', 'she', 'was', 'see', 'if', 'got', 'never', 'from', 'he', 'feel', 'want', 'let', 'make', 'way', 'say', 'take', 'would', 'as', 'ca', 'day', 'at', 'babi', 'away', 'life', 'yeah', 'y', 'back', 'by', 'her', 'heart', 'here', 'how', 'could', 'night', 'need', 'our', 'look', 'where', 'en', 'eye', 'thing', 'world', 'more', 'caus', 'gonna', 'die', 'right', 'been', 'tell', 'think', 'un', 'who', 'el', 'through', 'man', 'live', 'again', 'give', 'too', 'onli', 'te', 'tri', 'tu', 'or', 'whi', 'se', 'keep', 'dream', 'well', 'mind', 'an', 'wo', 'still', 'us', 'his', 'long', 'mi', 'girl', 'wanna', 'find', 'fall', 'around', 'good', 'about', 'some', 'ov

In [19]:
# Read release info
release_info = []

f1 = open('tracks_per_year.txt','r')
release_info = f1.readlines()
f1.close()

In [40]:
# Song year and ID can be extracted like this:
song = release_info[1]
print(song)
year = song[0:4] 
l = len('TRMYDFV128F42511FC') 
tag = song[9:27]
print(year)
print(tag)

1922<SEP>TRMYDFV128F42511FC<SEP>Barrington Levy<SEP>Warm And Sunny Day

1922
TRMYDFV128F42511FC


In [82]:
# create dictionary of release year & song id
release_years = {}

for song in release_info:
    year = song[0:4]
    tag = song[9:27]
    release_years[tag] = year
        

In [ ]:
# links lyrics to release year ? 
# 154527 usable songs, found by looping & counting, 5000 total words 
# each set of lyrics will be a 5000-element array w/ # of uses @ index of the word 
n_songs = 154527
years_lyrics_pairs =  pd.DataFrame({'Lyrics' : 'LYRICS GO HERE',
                                    'Year' : 1.},
                                   index=list(range(n_songs)))



In [95]:
# converts years to decade

def year_group(year, group_by): 
    group = -1
    
    if group_by == 'five_years':
        if year >= 1960 and year <= 1969:
            group = 0
        elif year >= 1970 and year <= 1974:
            group = 1
        elif year >= 1975 and year <= 1979:
            group = 2
        elif year >= 1980 and year <= 1984:
            group = 3
        elif year >= 1985 and year <= 1989:
            group = 4
        elif year >= 1990 and year <= 1994:
            group = 5
        elif year >= 1995 and year <= 1999:
            group = 6
        elif year >= 2000 and year <= 2004:
            group = 7
        elif year >= 2005 and year <= 2009:
            group = 8
        elif year >= 2010 and year <= 2014:
            group = 9
        elif year >= 2015:
            group = 10
    elif group_by == 'decade':
        if year >= 1960 and year <= 1969:
            group = 0
        elif year >= 1970 and year <= 1979:
            group = 1
        elif year >= 1980 and year <= 1989:
            group = 2
        elif year >= 1990 and year <= 1999:
            group = 3
        elif year >= 2000 and year <= 2009:
            group = 4
        elif year >= 2010:
            group = 5
    
    return group

In [157]:
# loop over each song we have lyrics for

import time

# Converts years to decade range 

# row of dataframe to store info in 
ind = 0

for song_info in lyrics_info: 
    song = song_info.split(',')
    song_tag = song[0]
    
    song_words_single_str = song
    
    t1 = time.time()
    
    if song_tag in release_years: 
        # check if year is between 1960 - 2019 
        song_year = release_years[song_tag]
        if int(song_year) >= 1960 and int(song_year) <= 2019:
            words_in_song = song[2:]
            # fixes last word, removes newline operator
            last_word = words_in_song[-1]
            last_word = last_word[0:-1]
            words_in_song[-1] = last_word
            
            this_song_lyrics = '' # append lyrics here
            
            # loop over words in song 
            for word_and_count in words_in_song:
                # get each word-count pair WORD:COUNT
                [word_ind, count] = word_and_count.split(':')
                word = word_list[int(word_ind) - 1]
                count = int(count)
                for i in range(count):
                    # concatenate WORD to lyrics list COUNT times 
                    this_song_lyrics = this_song_lyrics + word + ' '
                    
            # store lyrics list in df
            years_lyrics_pairs.loc[ind,'Lyrics'] = this_song_lyrics
            # store year in df
            years_lyrics_pairs.loc[ind,'Year'] = year_group(int(song_year),'decade')
            ind = ind + 1
            
            t2 = time.time()
            print('{}/{} done'.format(ind,n_songs))
        else:
            continue
    else:
        continue
    


1/154527 done
2/154527 done
3/154527 done
4/154527 done
5/154527 done
6/154527 done
7/154527 done
8/154527 done
9/154527 done
10/154527 done
11/154527 done
12/154527 done
13/154527 done
14/154527 done
15/154527 done
16/154527 done
17/154527 done
18/154527 done
19/154527 done
20/154527 done
21/154527 done
22/154527 done
23/154527 done
24/154527 done
25/154527 done
26/154527 done
27/154527 done
28/154527 done
29/154527 done
30/154527 done
31/154527 done
32/154527 done
33/154527 done
34/154527 done
35/154527 done
36/154527 done
37/154527 done
38/154527 done
39/154527 done
40/154527 done
41/154527 done
42/154527 done
43/154527 done
44/154527 done
45/154527 done
46/154527 done
47/154527 done
48/154527 done
49/154527 done
50/154527 done
51/154527 done
52/154527 done
53/154527 done
54/154527 done
55/154527 done
56/154527 done
57/154527 done
58/154527 done
59/154527 done
60/154527 done
61/154527 done
62/154527 done
63/154527 done
64/154527 done
65/154527 done
66/154527 done
67/154527 done
68/1

536/154527 done
537/154527 done
538/154527 done
539/154527 done
540/154527 done
541/154527 done
542/154527 done
543/154527 done
544/154527 done
545/154527 done
546/154527 done
547/154527 done
548/154527 done
549/154527 done
550/154527 done
551/154527 done
552/154527 done
553/154527 done
554/154527 done
555/154527 done
556/154527 done
557/154527 done
558/154527 done
559/154527 done
560/154527 done
561/154527 done
562/154527 done
563/154527 done
564/154527 done
565/154527 done
566/154527 done
567/154527 done
568/154527 done
569/154527 done
570/154527 done
571/154527 done
572/154527 done
573/154527 done
574/154527 done
575/154527 done
576/154527 done
577/154527 done
578/154527 done
579/154527 done
580/154527 done
581/154527 done
582/154527 done
583/154527 done
584/154527 done
585/154527 done
586/154527 done
587/154527 done
588/154527 done
589/154527 done
590/154527 done
591/154527 done
592/154527 done
593/154527 done
594/154527 done
595/154527 done
596/154527 done
597/154527 done
598/1545

1049/154527 done
1050/154527 done
1051/154527 done
1052/154527 done
1053/154527 done
1054/154527 done
1055/154527 done
1056/154527 done
1057/154527 done
1058/154527 done
1059/154527 done
1060/154527 done
1061/154527 done
1062/154527 done
1063/154527 done
1064/154527 done
1065/154527 done
1066/154527 done
1067/154527 done
1068/154527 done
1069/154527 done
1070/154527 done
1071/154527 done
1072/154527 done
1073/154527 done
1074/154527 done
1075/154527 done
1076/154527 done
1077/154527 done
1078/154527 done
1079/154527 done
1080/154527 done
1081/154527 done
1082/154527 done
1083/154527 done
1084/154527 done
1085/154527 done
1086/154527 done
1087/154527 done
1088/154527 done
1089/154527 done
1090/154527 done
1091/154527 done
1092/154527 done
1093/154527 done
1094/154527 done
1095/154527 done
1096/154527 done
1097/154527 done
1098/154527 done
1099/154527 done
1100/154527 done
1101/154527 done
1102/154527 done
1103/154527 done
1104/154527 done
1105/154527 done
1106/154527 done
1107/154527 do

1538/154527 done
1539/154527 done
1540/154527 done
1541/154527 done
1542/154527 done
1543/154527 done
1544/154527 done
1545/154527 done
1546/154527 done
1547/154527 done
1548/154527 done
1549/154527 done
1550/154527 done
1551/154527 done
1552/154527 done
1553/154527 done
1554/154527 done
1555/154527 done
1556/154527 done
1557/154527 done
1558/154527 done
1559/154527 done
1560/154527 done
1561/154527 done
1562/154527 done
1563/154527 done
1564/154527 done
1565/154527 done
1566/154527 done
1567/154527 done
1568/154527 done
1569/154527 done
1570/154527 done
1571/154527 done
1572/154527 done
1573/154527 done
1574/154527 done
1575/154527 done
1576/154527 done
1577/154527 done
1578/154527 done
1579/154527 done
1580/154527 done
1581/154527 done
1582/154527 done
1583/154527 done
1584/154527 done
1585/154527 done
1586/154527 done
1587/154527 done
1588/154527 done
1589/154527 done
1590/154527 done
1591/154527 done
1592/154527 done
1593/154527 done
1594/154527 done
1595/154527 done
1596/154527 do

2022/154527 done
2023/154527 done
2024/154527 done
2025/154527 done
2026/154527 done
2027/154527 done
2028/154527 done
2029/154527 done
2030/154527 done
2031/154527 done
2032/154527 done
2033/154527 done
2034/154527 done
2035/154527 done
2036/154527 done
2037/154527 done
2038/154527 done
2039/154527 done
2040/154527 done
2041/154527 done
2042/154527 done
2043/154527 done
2044/154527 done
2045/154527 done
2046/154527 done
2047/154527 done
2048/154527 done
2049/154527 done
2050/154527 done
2051/154527 done
2052/154527 done
2053/154527 done
2054/154527 done
2055/154527 done
2056/154527 done
2057/154527 done
2058/154527 done
2059/154527 done
2060/154527 done
2061/154527 done
2062/154527 done
2063/154527 done
2064/154527 done
2065/154527 done
2066/154527 done
2067/154527 done
2068/154527 done
2069/154527 done
2070/154527 done
2071/154527 done
2072/154527 done
2073/154527 done
2074/154527 done
2075/154527 done
2076/154527 done
2077/154527 done
2078/154527 done
2079/154527 done
2080/154527 do

...

152766/154527 done
152767/154527 done
152768/154527 done
152769/154527 done
152770/154527 done
152771/154527 done
152772/154527 done
152773/154527 done
152774/154527 done
152775/154527 done
152776/154527 done
152777/154527 done
152778/154527 done
152779/154527 done
152780/154527 done
152781/154527 done
152782/154527 done
152783/154527 done
152784/154527 done
152785/154527 done
152786/154527 done
152787/154527 done
152788/154527 done
152789/154527 done
152790/154527 done
152791/154527 done
152792/154527 done
152793/154527 done
152794/154527 done
152795/154527 done
152796/154527 done
152797/154527 done
152798/154527 done
152799/154527 done
152800/154527 done
152801/154527 done
152802/154527 done
152803/154527 done
152804/154527 done
152805/154527 done
152806/154527 done
152807/154527 done
152808/154527 done
152809/154527 done
152810/154527 done
152811/154527 done
152812/154527 done
152813/154527 done
152814/154527 done
152815/154527 done
152816/154527 done
152817/154527 done
152818/15452

153202/154527 done
153203/154527 done
153204/154527 done
153205/154527 done
153206/154527 done
153207/154527 done
153208/154527 done
153209/154527 done
153210/154527 done
153211/154527 done
153212/154527 done
153213/154527 done
153214/154527 done
153215/154527 done
153216/154527 done
153217/154527 done
153218/154527 done
153219/154527 done
153220/154527 done
153221/154527 done
153222/154527 done
153223/154527 done
153224/154527 done
153225/154527 done
153226/154527 done
153227/154527 done
153228/154527 done
153229/154527 done
153230/154527 done
153231/154527 done
153232/154527 done
153233/154527 done
153234/154527 done
153235/154527 done
153236/154527 done
153237/154527 done
153238/154527 done
153239/154527 done
153240/154527 done
153241/154527 done
153242/154527 done
153243/154527 done
153244/154527 done
153245/154527 done
153246/154527 done
153247/154527 done
153248/154527 done
153249/154527 done
153250/154527 done
153251/154527 done
153252/154527 done
153253/154527 done
153254/15452

153637/154527 done
153638/154527 done
153639/154527 done
153640/154527 done
153641/154527 done
153642/154527 done
153643/154527 done
153644/154527 done
153645/154527 done
153646/154527 done
153647/154527 done
153648/154527 done
153649/154527 done
153650/154527 done
153651/154527 done
153652/154527 done
153653/154527 done
153654/154527 done
153655/154527 done
153656/154527 done
153657/154527 done
153658/154527 done
153659/154527 done
153660/154527 done
153661/154527 done
153662/154527 done
153663/154527 done
153664/154527 done
153665/154527 done
153666/154527 done
153667/154527 done
153668/154527 done
153669/154527 done
153670/154527 done
153671/154527 done
153672/154527 done
153673/154527 done
153674/154527 done
153675/154527 done
153676/154527 done
153677/154527 done
153678/154527 done
153679/154527 done
153680/154527 done
153681/154527 done
153682/154527 done
153683/154527 done
153684/154527 done
153685/154527 done
153686/154527 done
153687/154527 done
153688/154527 done
153689/15452

154070/154527 done
154071/154527 done
154072/154527 done
154073/154527 done
154074/154527 done
154075/154527 done
154076/154527 done
154077/154527 done
154078/154527 done
154079/154527 done
154080/154527 done
154081/154527 done
154082/154527 done
154083/154527 done
154084/154527 done
154085/154527 done
154086/154527 done
154087/154527 done
154088/154527 done
154089/154527 done
154090/154527 done
154091/154527 done
154092/154527 done
154093/154527 done
154094/154527 done
154095/154527 done
154096/154527 done
154097/154527 done
154098/154527 done
154099/154527 done
154100/154527 done
154101/154527 done
154102/154527 done
154103/154527 done
154104/154527 done
154105/154527 done
154106/154527 done
154107/154527 done
154108/154527 done
154109/154527 done
154110/154527 done
154111/154527 done
154112/154527 done
154113/154527 done
154114/154527 done
154115/154527 done
154116/154527 done
154117/154527 done
154118/154527 done
154119/154527 done
154120/154527 done
154121/154527 done
154122/15452

154505/154527 done
154506/154527 done
154507/154527 done
154508/154527 done
154509/154527 done
154510/154527 done
154511/154527 done
154512/154527 done
154513/154527 done
154514/154527 done
154515/154527 done
154516/154527 done
154517/154527 done
154518/154527 done
154519/154527 done
154520/154527 done
154521/154527 done
154522/154527 done
154523/154527 done
154524/154527 done
154525/154527 done
154526/154527 done
154527/154527 done


In [158]:
print('finally done!')

finally done!


In [159]:
years_lyrics_pairs.to_csv(r'dataset_million.csv')

In [ ]:
# loop over each song we have lyrics for

import time

# Converts years to decade range 

# row of dataframe to store info in 
ind = 0

for song_info in lyrics_info: 
    song = song_info.split(',')
    song_tag = song[0]
    
    song_words_single_str = song
    
    t1 = time.time()
    
    if song_tag in release_years: 
        # check if year is between 1960 - 2019 
        song_year = release_years[song_tag]
        if int(song_year) >= 1960 and int(song_year) <= 2019:
            words_in_song = song[2:]
            # fixes last word, removes newline operator
            last_word = words_in_song[-1]
            last_word = last_word[0:-1]
            words_in_song[-1] = last_word
            
            this_song_lyrics = '' # append lyrics here
            
            # loop over words in song 
            for word_and_count in words_in_song:
                # get each word-count pair WORD:COUNT
                [word_ind, count] = word_and_count.split(':')
                word = word_list[int(word_ind) - 1]
                count = int(count)
                for i in range(count):
                    # concatenate WORD to lyrics list COUNT times 
                    this_song_lyrics = this_song_lyrics + word + ' '
                    
            # store lyrics list in df
            years_lyrics_pairs.loc[ind,'Lyrics'] = this_song_lyrics
            # store year in df
            years_lyrics_pairs.loc[ind,'Year'] = year_group(int(song_year),'decade')
            ind = ind + 1
            
            t2 = time.time()
            print('{}/{} done'.format(ind,n_songs))
        else:
            continue
    else:
        continue
    
